In [1]:
# Importar las librerías necesarias
import pandas as pd
import numpy as np
import sweetviz as sv
import seaborn as sns
import matplotlib.pyplot as plt
from joblib import Parallel, delayed
import warnings
from scipy.stats import zscore, mode
from sklearn.metrics import (silhouette_samples,silhouette_score,make_scorer,mean_absolute_error, r2_score, mean_squared_error,accuracy_score,precision_score,recall_score,f1_score,roc_auc_score)
from sklearn.base import (BaseEstimator,TransformerMixin,ClassifierMixin,RegressorMixin)
from sklearn.pipeline import Pipeline
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, BaseCrossValidator, KFold, cross_val_score, RandomizedSearchCV, GridSearchCV
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from xgboost import XGBRegressor
import joblib
from joblib import load
import os
from tslearn.preprocessing import TimeSeriesScalerMeanVariance
from tslearn.clustering import TimeSeriesKMeans, silhouette_score as ts_silhouette_score
import shap
from lime import lime_tabular
from sklearn.model_selection import GroupKFold

In [2]:
# Cargar los datos desde el archivo Excel
file_path = '/Users/sebastian/Desktop/Documents/Master Data Science/tesis/dataset_oct_2014-set_2024_sin dlocal.xlsx'
df = pd.read_excel(file_path, sheet_name='dataset')

In [3]:
df.head()

Empresa     Fecha      P_E     P_B    P_TB     P_S     P_CF  \
0  FLWS US Equity  20140930  31.7207  2.5643  6.1415  0.6062  10.3190   
1  FLWS US Equity  20141031  35.4266  2.8638   6.859   0.677  11.5246   
2  FLWS US Equity  20141128  37.7207  3.0493  7.3032  0.7208  12.2709   
3  FLWS US Equity  20141231  11.3711  2.3843  8.1913  0.5153   2.6214   
4  FLWS US Equity  20150130  10.8881   2.283  7.8433  0.4934   2.5100   

     P_FCF P_Share   ROCE_sp  ...  Efectivo y equiv_l  CPI  CPI_Exp_mediana  \
0  21.6093    7.19  5.886400  ...            1.314000  1.7            0.019   
1  24.1339    8.03  8.881198  ...            2.610333  1.7            0.016   
2  25.6967    8.55  9.469145  ...            3.906667  1.3            0.016   
3   3.0449    8.24  8.721900  ...            5.203000  0.8            0.014   
4   2.9155    7.89  7.711122  ...            4.188000 -0.1            0.007   

   CPI_Exp_promedio  Fed Funds Rate  Fed Funds Rate_Exp_mediana  \
0            0.0191            0.25                      0.0025   
1            0.0162            0.25                      0.0025   
2            0.0157            0.25                      0.0025   
3            0.0142            0.25                      0.0025   
4            0.0069            0.25                      0.0025   

   Fed Funds Rate_Exp_promedio  Non farm payrolls  \
0                       0.0025                307   
1                       0.0025                240   
2                       0.0025                284   
3                       0.0025                278   
4                       0.0025                196   

   Non farm payrolls_Exp_mediana  Non farm payrolls_Exp_promedio  
0                           230k                         226.13k  
1                           215k                         216.22k  
2                           235k                         236.62k  
3                           230k                         229.16k  
4                           240k                         234.73k  

[5 rows x 42 columns]

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 166440 entries, 0 to 166439
Data columns (total 42 columns):
 #   Column                          Non-Null Count   Dtype  
---  ------                          --------------   -----  
 0   Empresa                         166440 non-null  object 
 1   Fecha                           166440 non-null  int64  
 2   P_E                             87792 non-null   float64
 3   P_B                             119348 non-null  object 
 4   P_TB                            92514 non-null   object 
 5   P_S                             117703 non-null  object 
 6   P_CF                            95713 non-null   float64
 7   P_FCF                           69291 non-null   object 
 8   P_Share                         131345 non-null  object 
 9   ROCE_sp                         115613 non-null  float64
 10  ROCE_l                          115613 non-null  float64
 11  EBIT_sp                         115176 non-null  float64
 12  EBIT_l          

In [5]:
# Quitar "k" de las columnas "Non farm payrolls_Exp_mediana" y "Non farm payrolls_Exp_promedio"
df['Non farm payrolls_Exp_mediana'] = df['Non farm payrolls_Exp_mediana'].astype(str).str.replace('k', '')
df['Non farm payrolls_Exp_promedio'] = df['Non farm payrolls_Exp_promedio'].astype(str).str.replace('k', '')

# Convertir las columnas a valores numéricos
df['Non farm payrolls_Exp_mediana'] = pd.to_numeric(df['Non farm payrolls_Exp_mediana'], errors='coerce')
df['Non farm payrolls_Exp_promedio'] = pd.to_numeric(df['Non farm payrolls_Exp_promedio'], errors='coerce')
df['P_B'] = pd.to_numeric(df['P_B'], errors='coerce')
df['P_TB'] = pd.to_numeric(df['P_TB'], errors='coerce')
df['P_S'] = pd.to_numeric(df['P_S'], errors='coerce')
df['P_FCF'] = pd.to_numeric(df['P_FCF'], errors='coerce')
df['P_Share'] = pd.to_numeric(df['P_Share'], errors='coerce')

In [6]:
# Convertir la columna de fecha a formato datetime
df['Fecha'] = pd.to_datetime(df['Fecha'], format='%Y%m%d')

# Extraer características temporales relevantes
df['mes'] = df['Fecha'].dt.month
df['año'] = df['Fecha'].dt.year
df['periodo'] = df['Fecha'].dt.to_period('M')

In [7]:
# Convertir CPI y Fed Funds Rate a decimales
df['CPI'] = df['CPI'] / 100
df['Fed Funds Rate'] = df['Fed Funds Rate'] / 100

In [8]:
# Calcular diferencias en puntos básicos
df['dif_CPI_mediana'] = (df['CPI'] - df['CPI_Exp_mediana']) * 10000
df['dif_CPI_promedio'] = (df['CPI'] - df['CPI_Exp_promedio']) * 10000

df['dif_FFR_mediana'] = (df['Fed Funds Rate'] - df['Fed Funds Rate_Exp_mediana']) * 10000
df['dif_FFR_promedio'] = (df['Fed Funds Rate'] - df['Fed Funds Rate_Exp_promedio']) * 10000

# Calcular diferencia
df['dif_NFP_mediana'] = (df['Non farm payrolls'] - df['Non farm payrolls_Exp_mediana'])
df['dif_NFP_promedio'] = (df['Non farm payrolls'] - df['Non farm payrolls_Exp_promedio'])

In [9]:
# Cargar tickers financieros (GICS)
gics_financieras = r'C:\Users\Andy\OneDrive\Desktop\MCD\Tesis\Datos_fuente_Bloomberg\GICS_Finanzas.xlsx'
try:
    df_tickers_financieras = pd.read_excel(gics_financieras)
    columna_ticker_excel = 'Ticker de miembro'
    columna_ticker_df = 'Ticker de miembro'

    if columna_ticker_excel not in df_tickers_financieras.columns:
        raise ValueError(f"La columna '{columna_ticker_excel}' no se encuentra en el archivo Excel.")

    # Seleccionar columna de tickers y renombrarla si es necesario para el merge
    df_tickers_financieras = df_tickers_financieras[[columna_ticker_excel]].rename(columns={columna_ticker_excel: columna_ticker_df})
    
    # Eliminar duplicados
    df_tickers_financieras = df_tickers_financieras.drop_duplicates().reset_index(drop=True)

    print(f"Se cargaron {len(df_tickers_financieras)} tickers del sector financiero.")
    print(df_tickers_financieras.head())

except FileNotFoundError:
    print(f"Error: No se encontró el archivo '{gics_financieras}'")
    
except ValueError as ve:
     print(f"Error al procesar el Excel: {ve}")
     
except Exception as e:
    print(f"Ocurrió un error inesperado al leer el Excel: {e}")
    

Se cargaron 6271 tickers del sector financiero.
  Ticker de miembro
0   BRK/A US Equity
1    8109 HK Equity
2     JPM US Equity
3  601398 CH Equity
4    1288 HK Equity


In [10]:
columna_ticker_df_en_principal = 'Empresa' 

# Obtener la lista de tickers financieros cargados
tickers_financieros_lista = df_tickers_financieras[df_tickers_financieras.columns[0]].unique()

# Verificar que la columna exista en df
if columna_ticker_df_en_principal not in df.columns:
    print(f"ERROR: La columna '{columna_ticker_df_en_principal}' no existe en el DataFrame principal 'df'.")
    print(f"Columnas disponibles en 'df': {df.columns.tolist()}")

else:
    # Filtrar df usando la lista de tickers
    df_financieras_completo = df[df[columna_ticker_df_en_principal].isin(tickers_financieros_lista)].copy()

    num_empresas_filtradas = df_financieras_completo[columna_ticker_df_en_principal].nunique()
    print(f"\nDataFrame filtrado ('df_financieras_completo') contiene:")
    print(f"  - {len(df_financieras_completo)} filas")
    print(f"  - {num_empresas_filtradas} empresas financieras únicas.")

    if df_financieras_completo.empty:
        print("\n¡ADVERTENCIA! El DataFrame filtrado está vacío.")
        print("Posibles causas:")
        print("  - No hay coincidencias entre los tickers del Excel y los tickers en la columna "
              f"'{columna_ticker_df_en_principal}' de 'df'.")
        print("  - Verifica los formatos de los tickers (ej. 'AAPL' vs 'AAPL US Equity').")
        print("  - Verifica que el nombre de la columna en 'df' sea correcto.")
    else:
        print("\nPrimeras filas del DataFrame filtrado ('df_financieras_completo'):")
        print(df_financieras_completo.head())
        print("\nÚltimas filas del DataFrame filtrado ('df_financieras_completo'):")
        print(df_financieras_completo.tail())



Filtrando el DataFrame principal ('df') para tickers financieros...
Se usarán los tickers de la columna 'Ticker de miembro' del archivo Excel.
Se buscarán coincidencias en la columna 'Empresa' del DataFrame principal.

DataFrame filtrado ('df_financieras_completo') contiene:
  - 27480 filas
  - 229 empresas financieras únicas.

Primeras filas del DataFrame filtrado ('df_financieras_completo'):
            Empresa      Fecha      P_E     P_B    P_TB     P_S     P_CF  \
360  SRCE US Equity 2014-09-30  12.5518  1.1270  1.3134  2.7127   9.6024   
361  SRCE US Equity 2014-10-31  13.7902  1.2382  1.4429  2.9804  10.5499   
362  SRCE US Equity 2014-11-28  13.4509  1.2077  1.4074  2.9070  10.2902   
363  SRCE US Equity 2014-12-31  15.3159  1.3324  1.5474  3.2150  11.1493   
364  SRCE US Equity 2015-01-30  13.2714  1.1545  1.3408  2.7858   9.6610   

     P_FCF  P_Share   ROCE_sp  ...  Non farm payrolls_Exp_promedio  mes   año  \
360    NaN  25.8909  9.522900  ...                          226.

In [11]:
# Lista de columnas numéricas para análisis con mensualización lineal de los ratios 
# y variables macroeconómicas calculadas con mediana
columnas_numericas_lineal_mediana= [
    'P_E',
    'P_B',
    'P_S',
    'P_Share',
    'ROCE_l',
    'EBIT_l',
    'Total Activos_l',
    'Deuda a LP_l',
    'ROA_l',
    'Beneficio neto_l',
    'ROI_l',
    'EV_l',
    'Cap de mercado_l',
    'Deuda a CP_l',
    'Efectivo y equiv_l',
    'dif_CPI_mediana',
    'dif_FFR_mediana',
    'dif_NFP_mediana'
]

In [12]:
# Lista de columnas numéricas para análisis con mensualización spline de los ratios 
# y variables macroeconómicas calculadas con mediana
columnas_numericas_spline_mediana = [
    'P_E',
    'P_B',
    'P_S',
    'P_Share',
    'ROCE_sp',
    'EBIT_sp',
    'Total Activos_sp',
    'Deuda a LP_sp',
    'ROA_sp',
    'Beneficio neto_sp',
    'ROI_sp',
    'EV_sp',
    'Cap de mercado_sp',
    'Deuda a CP_sp',
    'Efectivo y equiv_sp',
    'dif_CPI_mediana',
    'dif_FFR_mediana',
    'dif_NFP_mediana'
]

In [13]:
# Lista de columnas numéricas para análisis con mensualización lineal de los ratios 
# y variables macroeconómicas calculadas con promedio
columnas_numericas_lineal_promedio = [
    'P_E',
    'P_B',
    'P_S',
    'P_Share',
    'ROCE_l',
    'EBIT_l',
    'Total Activos_l',
    'Deuda a LP_l',
    'ROA_l',
    'Beneficio neto_l',
    'ROI_l',
    'EV_l',
    'Cap de mercado_l',
    'Deuda a CP_l',
    'Efectivo y equiv_l',
    'dif_CPI_promedio',
    'dif_FFR_promedio',
    'dif_NFP_promedio'
]

In [14]:
# Lista de columnas numéricas para análisis con mensualización spline de los ratios 
# y variables macroeconómicas calculadas con promedio
columnas_numericas_spline_promedio = [
    'P_E',
    'P_B',
    'P_S',
    'P_Share',
    'ROCE_sp',
    'EBIT_sp',
    'Total Activos_sp',
    'Deuda a LP_sp',
    'ROA_sp',
    'Beneficio neto_sp',
    'ROI_sp',
    'EV_sp',
    'Cap de mercado_sp',
    'Deuda a CP_sp',
    'Efectivo y equiv_sp',
    'dif_CPI_promedio',
    'dif_FFR_promedio',
    'dif_NFP_promedio'
]

In [15]:
listas_columnas = {
    'lineal_mediana': columnas_numericas_lineal_mediana,
    'spline_mediana': columnas_numericas_spline_mediana,
    'lineal_promedio': columnas_numericas_lineal_promedio,
    'spline_promedio': columnas_numericas_spline_promedio
}

In [16]:
listas_columnas

{'lineal_mediana': ['P_E',
  'P_B',
  'P_S',
  'P_Share',
  'ROCE_l',
  'EBIT_l',
  'Total Activos_l',
  'Deuda a LP_l',
  'ROA_l',
  'Beneficio neto_l',
  'ROI_l',
  'EV_l',
  'Cap de mercado_l',
  'Deuda a CP_l',
  'Efectivo y equiv_l',
  'dif_CPI_mediana',
  'dif_FFR_mediana',
  'dif_NFP_mediana'],
 'spline_mediana': ['P_E',
  'P_B',
  'P_S',
  'P_Share',
  'ROCE_sp',
  'EBIT_sp',
  'Total Activos_sp',
  'Deuda a LP_sp',
  'ROA_sp',
  'Beneficio neto_sp',
  'ROI_sp',
  'EV_sp',
  'Cap de mercado_sp',
  'Deuda a CP_sp',
  'Efectivo y equiv_sp',
  'dif_CPI_mediana',
  'dif_FFR_mediana',
  'dif_NFP_mediana'],
 'lineal_promedio': ['P_E',
  'P_B',
  'P_S',
  'P_Share',
  'ROCE_l',
  'EBIT_l',
  'Total Activos_l',
  'Deuda a LP_l',
  'ROA_l',
  'Beneficio neto_l',
  'ROI_l',
  'EV_l',
  'Cap de mercado_l',
  'Deuda a CP_l',
  'Efectivo y equiv_l',
  'dif_CPI_promedio',
  'dif_FFR_promedio',
  'dif_NFP_promedio'],
 'spline_promedio': ['P_E',
  'P_B',
  'P_S',
  'P_Share',
  'ROCE_sp',
  'E

In [17]:
# ┌─────────────────────────────────────────────────────────────────┐
# │ Importaciones y Funciones Auxiliares                            │
# └─────────────────────────────────────────────────────────────────┘
import pandas as pd
import numpy as np

def pct_missing_by_column(df, columns):
    """Devuelve % de NaNs por columna, ordenado descendente."""
    return (df[columns].isna().mean() * 100).sort_values(ascending=False)

def pct_missing_by_group(df, group_col, features):
    """Devuelve Series con el máximo % de NaNs en cualquier feature por grupo."""
    missing = df.groupby(group_col)[features]\
                .apply(lambda g: g.isna().mean()*100)
    return missing.max(axis=1)

def filter_companies_by_target_missing(df, group_col, target_col):
    """Filtra y devuelve df sin empresas que tengan ANY NaN en target_col."""
    ok = ~df.groupby(group_col)[target_col].apply(lambda s: s.isna().any())
    valid_companies = ok[ok].index
    return df[df[group_col].isin(valid_companies)].copy()

def impute_by_group(df, group_col, features, methods=('ffill',), fill_value=0): # <-- Cambiar default
    """Imputa NaNs por grupo usando .ffill() y termina con fillna(fill_value)."""
    df2 = df.sort_values([group_col, 'Fecha']).copy()
    for m in methods:
        df2[features] = df2.groupby(group_col)[features]\
                            .transform(lambda g: getattr(g, m)())
    return df2.fillna(fill_value)

def create_lags(df, group_col, date_col, features, lag=1):
    """Genera columnas de lag para cada feature dentro de cada grupo."""
    df2 = df.sort_values([group_col, date_col]).copy()
    for feat in features:
        df2[f"{feat}_lag{lag}"] = df2.groupby(group_col)[feat].shift(lag)
    return df2


In [18]:
# ┌─────────────────────────────────────────────────────────────────┐
# │  Filtrar Empresas Financieras                                   │
# └─────────────────────────────────────────────────────────────────┘
# Asume: df y df_tickers_financieras ya cargados, con la columna ticker en df_tickers_financieras.columns[0]
ticker_col = df_tickers_financieras.columns[0]
df_fin = df[df['Empresa'].isin(df_tickers_financieras[ticker_col].unique())].copy()
print(f"Empresas financieras: {df_fin['Empresa'].nunique()} únicas, {len(df_fin)} filas")


Empresas financieras: 229 únicas, 27480 filas


In [20]:
# ┌─────────────────────────────────────────────────────────────────┐
# │ Conversión a numérico                                    │
# └─────────────────────────────────────────────────────────────────┘
# Crear set de features base (sin 'Empresa' ni 'Fecha'), añadir 'P_E' si existe
features_base = {
    col for cols in listas_columnas.values()
            for col in cols if col not in ('Empresa','Fecha')
}
if 'P_E' in df_fin.columns:
    features_base.add('P_E')
numeric_cols = [c for c in sorted(features_base) if c in df_fin.columns]

# Vectorizado
nan_before = df_fin[numeric_cols].isna().sum()
df_fin[numeric_cols] = df_fin[numeric_cols].apply(pd.to_numeric, errors='coerce')
nan_after = df_fin[numeric_cols].isna().sum()
print("NaNs añadidos:", (nan_after - nan_before).sum())

NaNs añadidos: 0


In [22]:
# ┌─────────────────────────────────────────────────────────────────┐
# │ Excluir Columnas con Demasiados NaNs                            │
# └─────────────────────────────────────────────────────────────────┘
col_pct = pct_missing_by_column(df_fin, numeric_cols)
umbral_col = 30.0   # % máximo de NaNs tolerable
cols_to_exclude = col_pct[col_pct > umbral_col].index.tolist()
features_kept = [c for c in numeric_cols if c not in cols_to_exclude]
print(f"Columnas excluidas (> {umbral_col}% NaNs):", cols_to_exclude)


Columnas excluidas (> 30.0% NaNs): ['EBIT_l', 'EBIT_sp', 'EV_l', 'EV_sp']


In [23]:
# ┌─────────────────────────────────────────────────────────────────┐
# │ Filtrar Empresas con NaNs en el Target P_E                      │
# └─────────────────────────────────────────────────────────────────┘
df_fin_no_PE_NaN = filter_companies_by_target_missing(df_fin, 'Empresa', 'P_E')
print("Empresas tras filtrar P_E NaN:", df_fin_no_PE_NaN['Empresa'].nunique())


Empresas tras filtrar P_E NaN: 133


In [24]:
# ┌─────────────────────────────────────────────────────────────────┐
# │ Excluir Empresas con Demasiados NaNs en Features                │
# └─────────────────────────────────────────────────────────────────┘
umbral_grp = 10.0   # % máximo de NaNs por empresa
grp_pct = pct_missing_by_group(df_fin_no_PE_NaN, 'Empresa', features_kept)
empresas_final = grp_pct[grp_pct <= umbral_grp].index.tolist()
df_fin_final = df_fin_no_PE_NaN[df_fin_no_PE_NaN['Empresa'].isin(empresas_final)].copy()
print("Empresas finales (<= {umbral_grp}% NaNs):", len(empresas_final))


Empresas finales (<= {umbral_grp}% NaNs): 76


In [25]:
# ┌─────────────────────────────────────────────────────────────────┐
# │ Imputar NaNs Restantes                                          │
# └─────────────────────────────────────────────────────────────────┘
df_imputed = impute_by_group(df_fin_final, 'Empresa', features_kept)
print("NaNs totales después de imputar:", df_imputed[features_kept].isna().sum().sum())


NaNs totales después de imputar: 0


In [26]:
# ┌─────────────────────────────────────────────────────────────────┐
# │  Crear DataFrames con Lag (corregido)                           │
# └─────────────────────────────────────────────────────────────────┘
dfs_shifted = {}
for metodo, cols in listas_columnas.items():
    # Excluir P_E de la lista de feats para no duplicarlo
    feats = [c for c in cols 
             if c in df_imputed.columns 
             and c not in ('Empresa', 'Fecha', 'P_E')]
    if not feats:
        print(f"{metodo}: no hay features para lag; se omite.")
        continue

    # Preparamos el df base con IDs + target + características
    df_base = df_imputed[['Empresa', 'Fecha', 'P_E'] + feats].copy()

    # Generamos los lags
    df_lagged = create_lags(df_base, 'Empresa', 'Fecha', feats, lag=1)

    # Eliminamos filas donde cualquier lag sea NaN
    df_lagged.dropna(subset=[f"{f}_lag1" for f in feats], inplace=True)

    dfs_shifted[metodo] = df_lagged
    print(f"{metodo}: {df_lagged.shape[0]} filas, {df_lagged.shape[1]} columnas")



lineal_mediana: 9044 filas, 37 columnas
spline_mediana: 9044 filas, 37 columnas
lineal_promedio: 9044 filas, 37 columnas
spline_promedio: 9044 filas, 37 columnas


In [28]:
# ┌─────────────────────────────────────────────────────────────────┐
# │  Importaciones                                                  │
# └─────────────────────────────────────────────────────────────────┘

import warnings
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import time # Para medir tiempo

# importo modelos
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor

# importo métricas y preprocesamiento
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score, make_scorer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.model_selection import BaseCrossValidator, train_test_split, GridSearchCV, KFold
from sklearn.pipeline import Pipeline

# Ignorar warnings comunes
warnings.filterwarnings('ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=UserWarning)
pd.options.mode.chained_assignment = None

# ┌─────────────────────────────────────────────────────────────────┐
# │  FUNCIONES AUXILIARES (Con mejoras de robustez)                 │
# └─────────────────────────────────────────────────────────────────┘


def rmse(y_true, y_pred):
    """Calcula RMSE manejando NaNs/Infs"""
    y_true = np.asarray(y_true); y_pred = np.asarray(y_pred)
    mask = np.isfinite(y_true) & np.isfinite(y_pred)
    if not np.all(mask): y_true, y_pred = y_true[mask], y_pred[mask]
    if len(y_true) == 0: return np.nan
    return np.sqrt(mean_squared_error(y_true, y_pred))

rmse_scorer = make_scorer(rmse, greater_is_better=False)

class DropColumns(BaseEstimator, TransformerMixin):
    """Transformer para eliminar columnas especificadas en un Pipeline"""
    def __init__(self, columns=None): self.columns = columns
    def fit(self, X, y=None): return self
    def transform(self, X):
        if not isinstance(X, pd.DataFrame): return X
        return X.drop(columns=self.columns, errors='ignore')

class GroupTimeSeriesSplit(BaseCrossValidator):
    """Validador Cruzado tipo K-Fold Agrupado"""
    def __init__(self, n_splits=3): self.n_splits = n_splits
    def split(self, X, y=None, groups=None):
        if groups is None: raise ValueError("groups no puede ser None")
        groups = np.asarray(groups); unique_groups, idx = np.unique(groups, return_index=True)
        unique_groups = unique_groups[np.argsort(idx)]; n_groups = len(unique_groups)
        effective_n_splits = min(self.n_splits, n_groups)
        if effective_n_splits < 2: raise ValueError(f"No hay suficientes grupos ({n_groups}) para al menos 2 splits")
        if effective_n_splits != self.n_splits: print(f"    Advertencia GroupTimeSeriesSplit: Reduciendo n_splits a {effective_n_splits} debido a solo {n_groups} grupos.")
        fold_indices = np.array_split(np.arange(n_groups), effective_n_splits)
        for i in range(effective_n_splits):
            test_groups = unique_groups[fold_indices[i]]
            train_groups = unique_groups[np.concatenate([fold_indices[j] for j in range(effective_n_splits) if i != j])]
            test_idx = np.where(np.isin(groups, test_groups))[0]; train_idx = np.where(np.isin(groups, train_groups))[0]
            yield train_idx, test_idx
    def get_n_splits(self, X=None, y=None, groups=None):
         if groups is None: return self.n_splits
         groups = np.asarray(groups); n_groups = len(np.unique(groups))
         return min(self.n_splits, n_groups) if n_groups >= 2 else 0

#Definimos train_test

def train_test_split_by_empresa(df_model, n_empresas_prueba):
    """Divide los datos por empresa, asegurando un mínimo para entrenar."""
    if 'Empresa' not in df_model.columns: raise KeyError("'Empresa' necesaria")
    empresas_unicas = df_model['Empresa'].unique()
    n_total_empresas = len(empresas_unicas)

    if not isinstance(n_empresas_prueba, int) or n_empresas_prueba < 1:
         print(f"Advertencia train_test_split: n_empresas_prueba ({n_empresas_prueba}) debe ser un entero >= 1. Usando 1.")
         n_empresas_prueba = 1

    if n_empresas_prueba >= n_total_empresas - 1:
        print(f"Advertencia train_test_split: n_empresas_prueba ({n_empresas_prueba}) es demasiado alto para {n_total_empresas} empresas. Se necesitan al menos 2 para entrenar. Reduciendo n_empresas_prueba.")
        n_empresas_prueba = max(1, n_total_empresas - 2) # Dejar al menos 2 en train
        if n_empresas_prueba == 0: 
             print("ERROR train_test_split: No hay suficientes empresas para separar train y test.")
             return None, None, None, None

    empresas_entrenamiento, empresas_prueba = train_test_split(empresas_unicas, test_size=n_empresas_prueba, random_state=42)
    mask_entrenamiento = df_model['Empresa'].isin(empresas_entrenamiento); mask_prueba = df_model['Empresa'].isin(empresas_prueba)
    if 'P_E' not in df_model.columns: raise KeyError("'P_E' necesaria")
    X = df_model.drop(columns=['P_E']); y = df_model['P_E']
    X_train, y_train = X[mask_entrenamiento].copy(), y[mask_entrenamiento].copy()
    X_test, y_test = X[mask_prueba].copy(), y[mask_prueba].copy()
    if X_train.empty or X_test.empty: return None, None, None, None
    return X_train, y_train, X_test, y_test

#Definimos evaluacion del modelo

def evaluate_model(y_test, y_pred):
    """ Retorna métricas manejando NaNs/Infs."""
    y_test, y_pred = np.asarray(y_test), np.asarray(y_pred)
    mask = np.isfinite(y_test) & np.isfinite(y_pred)
    if not np.all(mask): y_test, y_pred = y_test[mask], y_pred[mask]
    if len(y_test) == 0: return {'RMSE': np.nan, 'MAE': np.nan, 'R2': np.nan}
    mae = mean_absolute_error(y_test, y_pred); rmse_val = rmse(y_test, y_pred)
    r2 = np.nan
    if np.var(y_test) > 1e-9:
         try: r2 = r2_score(y_test, y_pred)
         except ValueError: pass
    elif mean_squared_error(y_test, y_pred) < 1e-9: r2 = 1.0
    else: r2 = 0.0
    return {'RMSE': rmse_val, 'MAE': mae, 'R2': r2}

#Ordenamos por timestep

def sort_by_timestep(X, y):
    """Ordena X e y según 'time_step'"""
    if 'time_step' not in X.columns: return X, y
    if not isinstance(y, pd.Series) or not y.index.equals(X.index):
        if len(y) == len(X): y = pd.Series(y, index=X.index, name=getattr(y, 'name', 'target'))
        else: print("Error sort_by_timestep: y no alineable."); return X, y
    X_sorted = X.copy().sort_values('time_step'); y_sorted = y.loc[X_sorted.index]
    return X_sorted, y_sorted

#Grafica por importancia de features

def plot_feature_importances(model, feature_names, title="Importancia de Características"):
    """Grafica importancia de features"""
    try:
        estimator = model.steps[-1][1] if hasattr(model, 'steps') else model
        if not hasattr(estimator, 'feature_importances_'): return None
        importances = estimator.feature_importances_
        names = getattr(estimator, 'feature_names_in_', feature_names)
        if len(names) != len(importances): names = feature_names
        if len(names) != len(importances): return None
        fi_df = pd.DataFrame({'feature': names, 'importance': importances}).sort_values('importance', ascending=False)
        top_n = 30; fi_df = fi_df.head(top_n)
        plt.figure(figsize=(10, max(5, len(fi_df) * 0.3))); plt.barh(fi_df['feature'], fi_df['importance'])
        plt.xlabel('Importancia'); plt.ylabel('Característica'); plt.title(title); plt.gca().invert_yaxis(); plt.tight_layout(); plt.show()
        return fi_df
    except Exception as e: print(f"Error graficando importancia: {e}"); return None



# ┌─────────────────────────────────────────────────────────────────┐
# │  BLOQUE DE EXPERIMENTOS                                         │
# └─────────────────────────────────────────────────────────────────┘

# ASUME dfs_shifted_financieras contiene DataFrames con lag1 y NaNs manejados (dropna)
# ASUME listas_columnas está definido (aunque no se usa activamente)


results = []
start_time_total = time.time()
use_log_transform = True
test_size_ratio = 0.20 # <-- porcentaje para test

# Iterar sobre los métodos
for metodo, df_lag1 in dfs_shifted.items(): 
    start_time_config = time.time()
    key = metodo; lag_config_str = 'lag1'; k_warmup = 0 # k=0 porque usamos dropna

    print("\n" + "="*60)
    print(f"Procesando Método: {metodo} {'(CON Log Transform)' if use_log_transform else '(SIN Log Transform)'} (Lag 1, dropna)")
    print("="*60 + "\n")

    # Preparar df_model
    df_model = df_lag1.copy()
    if 'time_step' not in df_model.columns:
        df_model.sort_values(['Empresa', 'Fecha'], inplace=True)
        df_model['time_step'] = df_model.groupby('Empresa').cumcount()

    all_predictors_lag1 = sorted([col for col in df_model.columns if col.endswith('_lag1')])
    if not all_predictors_lag1: print(f"Advertencia: No lags _lag1 para {metodo}. Saltando."); continue

    # Split de Datos con Ratio
    n_total_empresas_metodo = df_model['Empresa'].nunique()

    # Calcular número de empresas para prueba
    n_empresas_prueba_calc = max(1, int(np.round(n_total_empresas_metodo * test_size_ratio)))

    # Asegurar mínimo en train
    if n_empresas_prueba_calc >= n_total_empresas_metodo - 1:
        n_empresas_prueba_calc = max(1, n_total_empresas_metodo - 2)

    print(f"    Total empresas para {metodo}: {n_total_empresas_metodo}")
    print(f"    Calculando split con test_size ~{test_size_ratio:.0%}: {n_empresas_prueba_calc} empresas para prueba.")

    X_train, y_train, X_test, y_test = train_test_split_by_empresa(df_model, n_empresas_prueba_calc)
    if X_train is None: print(f"Split fallido para {metodo}. Saltando."); continue
    print(f"    Split resultante: {X_train['Empresa'].nunique()} empresas train, {X_test['Empresa'].nunique()} empresas test.")

    # Log Transform
    y_train_target = None
    if use_log_transform:
        print("    Aplicando log1p a y_train...")
        y_train_numeric = pd.to_numeric(y_train, errors='coerce').fillna(0)
        if (y_train_numeric <= -1).any(): print(f"ERROR: y_train <= -1 en {metodo}. Saltando."); continue
        y_train_target = np.log1p(y_train_numeric)
        if not np.all(np.isfinite(y_train_target)): print(f"ERROR: y_train_target con NaNs/Infs en {metodo}. Saltando."); continue
    else:
        y_train_target = y_train

    # Features y datos ordenados
    features_for_model = all_predictors_lag1
    y_test_original = y_test.copy()
    X_train_sorted, y_train_sorted_target = sort_by_timestep(X_train, y_train_target)
    X_test_sorted, y_test_sorted_original = sort_by_timestep(X_test, y_test_original)

    # Combinaciones para busqueda de Hyperparametros
    param_grid_rf = { 'rf__max_depth': [10, None], 'rf__min_samples_split': [5, 10], 'rf__n_estimators': [100] }
    param_grid_xgb = { 'xgb__n_estimators': [100, 200], 'xgb__max_depth': [3, 5], 'xgb__learning_rate': [0.1, 0.05]}
    param_grid_lgbm = { 'lgbm__n_estimators': [100, 200], 'lgbm__learning_rate': [0.1, 0.05], 'lgbm__max_depth': [3, 5], 'lgbm__num_leaves': [15, 31] }
    param_grid_cb = { 'cb__iterations': [100, 200], 'cb__learning_rate': [0.1, 0.05], 'cb__depth': [3, 5], 'cb__l2_leaf_reg': [1, 3] }

    # RF, XGB, LGBM, CB
    scenarios={
     'RF_Simple': {'model': RandomForestRegressor(random_state=42, n_jobs=-1), 'hp': False, 'vt': False},
     'RF_TV': {'model': RandomForestRegressor(random_state=42, n_jobs=-1), 'hp': False, 'vt': True},
     'RF_HP': {'model': RandomForestRegressor(random_state=42, n_jobs=-1), 'hp': True,  'vt': False, 'grid': param_grid_rf,   'prefix': 'rf'},
     'RF_TVHP': {'model': RandomForestRegressor(random_state=42, n_jobs=-1), 'hp': True,  'vt': True,  'grid': param_grid_rf,   'prefix': 'rf'},
     'XGB_Simple': {'model': XGBRegressor(random_state=42, n_jobs=-1),          'hp': False, 'vt': False},
     'XGB_TV': {'model': XGBRegressor(random_state=42, n_jobs=-1),          'hp': False, 'vt': True},
     'XGB_HP': {'model': XGBRegressor(random_state=42, n_jobs=-1),          'hp': True,  'vt': False, 'grid': param_grid_xgb,  'prefix': 'xgb'},
     'XGB_TVHP': {'model': XGBRegressor(random_state=42, n_jobs=-1),          'hp': True,  'vt': True,  'grid': param_grid_xgb,  'prefix': 'xgb'},
     'LGBM_Simple': {'model': LGBMRegressor(random_state=42, n_jobs=-1),         'hp': False, 'vt': False},
     'LGBM_TV': {'model': LGBMRegressor(random_state=42, n_jobs=-1),         'hp': False, 'vt': True},
     'LGBM_HP': {'model': LGBMRegressor(random_state=42, n_jobs=-1),         'hp': True,  'vt': False, 'grid': param_grid_lgbm, 'prefix': 'lgbm'},
     'LGBM_TVHP': {'model': LGBMRegressor(random_state=42, n_jobs=-1),         'hp': True,  'vt': True,  'grid': param_grid_lgbm, 'prefix': 'lgbm'},
     'CB_Simple': {'model': CatBoostRegressor(random_state=42, verbose=0, allow_writing_files=False), 'hp': False, 'vt': False},
     'CB_TV': {'model': CatBoostRegressor(random_state=42, verbose=0, allow_writing_files=False), 'hp': False, 'vt': True},
     'CB_HP': {'model': CatBoostRegressor(random_state=42, verbose=0, allow_writing_files=False), 'hp': True,  'vt': False, 'grid': param_grid_cb,   'prefix': 'cb'},
     'CB_TVHP': {'model': CatBoostRegressor(random_state=42, verbose=0, allow_writing_files=False), 'hp': True,  'vt': True,  'grid': param_grid_cb,   'prefix': 'cb'}
    }

    for nombre_escenario, config_escenario in scenarios.items():
        start_time_escenario = time.time()
        modelo_base = config_escenario['model']
        hp_search = config_escenario['hp']
        val_temp = config_escenario['vt']

        current_X_train = X_train_sorted if val_temp else X_train
        current_y_train = y_train_sorted_target if val_temp else y_train_target
        current_X_test = X_test_sorted if val_temp else X_test
        current_y_test_orig = y_test_sorted_original if val_temp else y_test_original

        cols_to_drop = [col for col in ['Empresa', 'Fecha', 'time_step'] if col in current_X_train.columns]
        steps = [('drop_columns', DropColumns(columns=cols_to_drop))]
        modelo_final = None
        best_params_found = {}

        try:
            if hp_search:
                steps.append((config_escenario['prefix'], modelo_base))
                pipeline = Pipeline(steps)
                param_grid = config_escenario['grid']
                # Ajustar n_splits para CV por grupo
                n_train_groups = current_X_train['Empresa'].nunique()
                n_splits_cv = min(4, n_train_groups) if n_train_groups >= 2 else 0

                if val_temp and n_splits_cv >= 2:
                    cv_strategy = GroupTimeSeriesSplit(n_splits=n_splits_cv)
                    groups_fit = current_X_train['Empresa'].copy()
                    fit_params_cv = {'groups': groups_fit}
                elif val_temp and n_splits_cv < 2:
                     print("No hay suficientes grupos en train para GroupTimeSeriesSplit. Usando KFold(3).")
                     cv_strategy = KFold(n_splits=3, shuffle=True, random_state=42)
                     fit_params_cv = {}
                else: # No val_temp
                    cv_strategy = 3 # KFold simple
                    fit_params_cv = {}

                # Usar n_jobs=1 para estabilidad inicial
                grid_search = GridSearchCV(estimator=pipeline, param_grid=param_grid, scoring=rmse_scorer,
                                           cv=cv_strategy, n_jobs=1, verbose=0, refit=True, error_score='raise')

                print(f"    GridSearchCV (CV strategy: {type(cv_strategy).__name__}, n_splits={getattr(cv_strategy, 'n_splits', cv_strategy)})...")
                grid_search.fit(current_X_train, current_y_train, **fit_params_cv)
                best_params_found = grid_search.best_params_
                print(f"    GridSearchCV completado. Mejores params: {best_params_found}")
                modelo_final = grid_search.best_estimator_
            else:
                steps.append(('model', modelo_base))
                pipeline = Pipeline(steps)
                print("    Entrenando modelo simple...")
                pipeline.fit(current_X_train, current_y_train)
                print("    Entrenamiento completado.")
                modelo_final = pipeline

            # Predicción
            print("    Realizando predicciones...")
            pred_raw = modelo_final.predict(current_X_test)
            print("    Predicciones completadas.")

            # Reversión
            y_pred_orig = None
            if use_log_transform:
                print("    Revirtiendo predicciones (expm1)...")
                with np.errstate(over='ignore', invalid='ignore'): y_pred_orig = np.expm1(pred_raw)
                if np.any(~np.isfinite(y_pred_orig)):
                    num_non_finite = (~np.isfinite(y_pred_orig)).sum()
                    print(f"    Advertencia: {num_non_finite} NaNs/Infs en expm1. Reemplazando con NaN.")
                    y_pred_orig[~np.isfinite(y_pred_orig)] = np.nan
            else:
                y_pred_orig = pred_raw

            # Evaluación (sin "warm-up" porque usamos dropna)
            print("    Evaluando modelo...")
            # Evaluar directamente sobre current_y_test_orig y y_pred_orig
            res_escenario = evaluate_model(current_y_test_orig, y_pred_orig)
            print(f"    Métricas {nombre_escenario}: {res_escenario}")

            # Guardar resultados
            res_escenario.update({
                'Modelo': nombre_escenario.split('_')[0], # RF, XGB, LGBM o CB
                'Validacion_Temp': val_temp, 'Busqueda_HP': hp_search,
                'Config_Key': key, 'Metodo': metodo, 'Lag_Config': lag_config_str,
                'Log_Transform': use_log_transform, 'k_warmup': k_warmup, # k_warmup es 0 aquí
                'Best_Params': best_params_found if hp_search else None,
                'pipeline': modelo_final # Guardar modelo final
            })
            results.append(res_escenario)

        except Exception as e_escenario:
            print(f"    ERROR durante el escenario {nombre_escenario} para {key}: {e_escenario}. Saltando.")
            results.append({
                'Modelo': nombre_escenario.split('_')[0], 'Validacion_Temp': val_temp, 'Busqueda_HP': hp_search,
                'Config_Key': key, 'Metodo': metodo, 'Lag_Config': lag_config_str, 'Log_Transform': use_log_transform,
                'k_warmup': k_warmup, 'RMSE': np.nan, 'MAE': np.nan, 'R2': np.nan,
                'Best_Params': None, 'pipeline': f'Error: {e_escenario}'
            })
            continue
        finally:
            end_time_escenario = time.time()
            print(f"    Tiempo escenario {nombre_escenario}: {end_time_escenario - start_time_escenario:.2f} seg.")

    end_time_config = time.time()
    print(f"\nTiempo total para método {metodo}: {end_time_config - start_time_config:.2f} seg.")


# ┌─────────────────────────────────────────────────────────────────┐
# │  CREAR TABLA DE RESULTADOS                                      │
# └─────────────────────────────────────────────────────────────────┘

if results:
    df_results_all_models = pd.DataFrame(results)
    print("\n" + "="*60)
    print("--- Resultados Finales (Todos los Modelos, Lag 1, Dropna, Log Transform) ---")
    print(f"Total de resultados generados: {len(df_results_all_models)}")
    print("Ordenado por RMSE (ascendente):")
    with pd.option_context('display.max_rows', None, 'display.max_columns', None, 'display.width', 1000):
        cols_display = ['Config_Key', 'Modelo', 'Validacion_Temp', 'Busqueda_HP', 'Log_Transform', 'Lag_Config', 'RMSE', 'MAE', 'R2', 'Best_Params']
        print(df_results_all_models.sort_values(by='RMSE', ascending=True, na_position='last')[cols_display])
else:
    print("\nNo se generaron resultados.")

end_time_total = time.time()
print(f"\nTiempo total de ejecución del bloque: {(end_time_total - start_time_total)/60:.2f} minutos")

print("\nTabla de Resultados:")
df_results_all_models


Procesando Método: lineal_mediana (CON Log Transform) (Lag 1, dropna)

    Total empresas para lineal_mediana: 76
    Calculando split con test_size ~20%: 15 empresas para prueba.
    Split resultante: 61 empresas train, 15 empresas test.
    Aplicando log1p a y_train...

  --- Ejecutando Escenario: RF_Simple ---
    Entrenando modelo simple...
    Entrenamiento completado.
    Realizando predicciones...
    Predicciones completadas.
    Revirtiendo predicciones (expm1)...
    Evaluando modelo...
    Métricas RF_Simple: {'RMSE': 4.082097449852013, 'MAE': 2.1908445074703886, 'R2': 0.4958534643515873}
    Tiempo escenario RF_Simple: 4.48 seg.

  --- Ejecutando Escenario: RF_TV ---
    Entrenando modelo simple...
    Entrenamiento completado.
    Realizando predicciones...
    Predicciones completadas.
    Revirtiendo predicciones (expm1)...
    Evaluando modelo...
    Métricas RF_TV: {'RMSE': 4.111050422319616, 'MAE': 2.188464534411776, 'R2': 0.4886766121701708}
    Tiempo escenario RF_

RMSE       MAE        R2 Modelo  Validacion_Temp  Busqueda_HP  \
0   4.082097  2.190845  0.495853     RF            False        False   
1   4.111050  2.188465  0.488677     RF             True        False   
2   4.068489  2.180682  0.499209     RF            False         True   
3   4.100600  2.171768  0.491273     RF             True         True   
4   3.702494  2.109594  0.585257    XGB            False        False   
..       ...       ...       ...    ...              ...          ...   
59  3.721035  2.080067  0.581093   LGBM             True         True   
60  2.975289  1.803992  0.732177     CB            False        False   
61  2.951204  1.791076  0.736495     CB             True        False   
62  3.092749  1.916721  0.710613     CB            False         True   
63  3.408568  2.012486  0.648493     CB             True         True   

         Config_Key           Metodo Lag_Config  Log_Transform  k_warmup  \
0    lineal_mediana   lineal_mediana       lag1           True         0   
1    lineal_mediana   lineal_mediana       lag1           True         0   
2    lineal_mediana   lineal_mediana       lag1           True         0   
3    lineal_mediana   lineal_mediana       lag1           True         0   
4    lineal_mediana   lineal_mediana       lag1           True         0   
..              ...              ...        ...            ...       ...   
59  spline_promedio  spline_promedio       lag1           True         0   
60  spline_promedio  spline_promedio       lag1           True         0   
61  spline_promedio  spline_promedio       lag1           True         0   
62  spline_promedio  spline_promedio       lag1           True         0   
63  spline_promedio  spline_promedio       lag1           True         0   

                                          Best_Params  \
0                                                None   
1                                                None   
2   {'rf__max_depth': None, 'rf__min_samples_split...   
3   {'rf__max_depth': None, 'rf__min_samples_split...   
4                                                None   
..                                                ...   
59  {'lgbm__learning_rate': 0.05, 'lgbm__max_depth...   
60                                               None   
61                                               None   
62  {'cb__depth': 3, 'cb__iterations': 200, 'cb__l...   
63  {'cb__depth': 5, 'cb__iterations': 200, 'cb__l...   

                                             pipeline  
0   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
1   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
2   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
3   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
4   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
..                                                ...  
59  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
60  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
61  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
62  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
63  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  

[64 rows x 13 columns]

In [29]:
print("\nTabla de Resultados:")
df_results_all_models


Tabla de Resultados:


RMSE       MAE        R2 Modelo  Validacion_Temp  Busqueda_HP  \
0   4.082097  2.190845  0.495853     RF            False        False   
1   4.111050  2.188465  0.488677     RF             True        False   
2   4.068489  2.180682  0.499209     RF            False         True   
3   4.100600  2.171768  0.491273     RF             True         True   
4   3.702494  2.109594  0.585257    XGB            False        False   
..       ...       ...       ...    ...              ...          ...   
59  3.721035  2.080067  0.581093   LGBM             True         True   
60  2.975289  1.803992  0.732177     CB            False        False   
61  2.951204  1.791076  0.736495     CB             True        False   
62  3.092749  1.916721  0.710613     CB            False         True   
63  3.408568  2.012486  0.648493     CB             True         True   

         Config_Key           Metodo Lag_Config  Log_Transform  k_warmup  \
0    lineal_mediana   lineal_mediana       lag1           True         0   
1    lineal_mediana   lineal_mediana       lag1           True         0   
2    lineal_mediana   lineal_mediana       lag1           True         0   
3    lineal_mediana   lineal_mediana       lag1           True         0   
4    lineal_mediana   lineal_mediana       lag1           True         0   
..              ...              ...        ...            ...       ...   
59  spline_promedio  spline_promedio       lag1           True         0   
60  spline_promedio  spline_promedio       lag1           True         0   
61  spline_promedio  spline_promedio       lag1           True         0   
62  spline_promedio  spline_promedio       lag1           True         0   
63  spline_promedio  spline_promedio       lag1           True         0   

                                          Best_Params  \
0                                                None   
1                                                None   
2   {'rf__max_depth': None, 'rf__min_samples_split...   
3   {'rf__max_depth': None, 'rf__min_samples_split...   
4                                                None   
..                                                ...   
59  {'lgbm__learning_rate': 0.05, 'lgbm__max_depth...   
60                                               None   
61                                               None   
62  {'cb__depth': 3, 'cb__iterations': 200, 'cb__l...   
63  {'cb__depth': 5, 'cb__iterations': 200, 'cb__l...   

                                             pipeline  
0   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
1   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
2   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
3   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
4   (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
..                                                ...  
59  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
60  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
61  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
62  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
63  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  

[64 rows x 13 columns]

In [30]:
# Elección entre modelos

def select_candidate_models(df, n=3):
    """
    Selecciona los n modelos candidatos basándose únicamente en el RMSE (de menor a mayor).
    """
    return df.sort_values('RMSE').head()

The history saving thread hit an unexpected error (OperationalError('database or disk is full')).History will not be written to the database.


In [31]:
# Candidatos a mejor modelo
top_candidates = select_candidate_models(df_results_all_models, n=3)
print("Top candidatos según RMSE")
top_candidates

Top candidatos según RMSE


RMSE       MAE        R2 Modelo  Validacion_Temp  Busqueda_HP  \
12  2.937135  1.780862  0.739002     CB            False        False   
61  2.951204  1.791076  0.736495     CB             True        False   
60  2.975289  1.803992  0.732177     CB            False        False   
29  2.980539  1.801812  0.731231     CB             True        False   
44  2.987606  1.801451  0.729955     CB            False        False   

         Config_Key           Metodo Lag_Config  Log_Transform  k_warmup  \
12   lineal_mediana   lineal_mediana       lag1           True         0   
61  spline_promedio  spline_promedio       lag1           True         0   
60  spline_promedio  spline_promedio       lag1           True         0   
29   spline_mediana   spline_mediana       lag1           True         0   
44  lineal_promedio  lineal_promedio       lag1           True         0   

   Best_Params                                           pipeline  
12        None  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
61        None  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
60        None  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
29        None  (DropColumns(columns=['Empresa', 'Fecha', 'tim...  
44        None  (DropColumns(columns=['Empresa', 'Fecha', 'tim...